In [1]:
import numpy as np

import sys
sys.path.append("../")
from koopmanlib.dictionary import PsiNN

In [2]:
basis_function = PsiNN(layer_sizes=[100,100,100], n_psi_train=100)

In [3]:
from duffing_oscillator import duffing_oscillator
from scipy.integrate import solve_ivp

# Parameters
delta = 0.5
alpha = -1
beta = 1

# Sample N=1000 initial points, with uniform distribution [-2, 2].
N = 1000
np.random.seed(39)
sample_data_x0 = (np.random.rand(N, 2) * 4) - 2

tspan = [0, 2.5]
nstep = 11
data = np.zeros((N, 2, nstep))

t_eval = np.linspace(tspan[0], tspan[1], nstep)

for idx, x0 in enumerate(sample_data_x0):
    sol = solve_ivp(duffing_oscillator, tspan, x0, t_eval=t_eval, args=(delta, alpha, beta))
    data[idx, 0, :] = sol.y[0]
    data[idx, 1, :] = sol.y[1]

# Pairwise shifted data X and Y
X = data[:, :, :-1] # shape: (1000, 2, 10)
Y = data[:, :, 1:]
print(X.shape, type(X))
print(Y.shape, type(Y))

# Transpose and reshape the data.
X = np.transpose(X, (0, 2, 1)).reshape(N * (nstep-1), 2) # shape: (10000, 2)
Y = np.transpose(Y, (0, 2, 1)).reshape(N * (nstep-1), 2)
print(X.shape, type(X))
print(Y.shape, type(Y))

(1000, 2, 10) <class 'numpy.ndarray'>
(1000, 2, 10) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>


In [4]:
len_all = X.shape[0]
data_x_train = X[:int(0.7*len_all),:]
data_x_valid = X[int(0.7*len_all)+1:,:]

data_y_train = Y[:int(0.7*len_all),:]
data_y_valid = Y[int(0.7*len_all)+1:,:]

In [5]:
data_train = [data_x_train, data_y_train]
data_valid = [data_x_valid, data_y_valid]

In [14]:
from koopmanlib.solver_0 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 148ms/step - loss: 0.0114 - val_loss: 0.0030
Epoch 2/2
2/2 [==============================] - 0s 36ms/step - loss: 0.0103 - val_loss: 0.0230
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 1s 686ms/step - loss: 4.8686e-04 - val_loss: 0.0016
Epoch 2/2
2/2 [==============================] - 0s 44ms/step - loss: 0.0013 - val_loss: 8.0857e-04
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 69ms/step - loss: 2.6879e-04 - val_loss: 9.3558e-04
Epoch 2/2
2/2 [==============================] - 0s 43ms/step - loss: 7.3194e-04 - val_loss: 3.6920e-04
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 61ms/step - loss: 1.9793e-04 - val_loss: 5.9394e-04
Epoch 2/2
2/2 [==============================] - 0s 38ms/step - loss: 4.7308e-04 - val_loss: 2.5077e-04
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 60ms/step - loss: 1.7112e-

In [15]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs0 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs0['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs0['resDMD_DL_outputs']['efuns'].shape)

[ 1.00768204e+00+0.00000000e+00j  1.00003302e+00+0.00000000e+00j
  8.18758201e-01+3.37582089e-01j  8.18758201e-01-3.37582089e-01j
  8.16484074e-01-1.45754196e-01j  8.16484074e-01+1.45754196e-01j
  8.07404503e-01+0.00000000e+00j  7.49572522e-01+3.84885565e-01j
  7.49572522e-01-3.84885565e-01j  5.40991647e-01+4.17512947e-01j
  5.40991647e-01-4.17512947e-01j  5.18967632e-01+0.00000000e+00j
  4.15256318e-01+0.00000000e+00j  3.41852322e-01+4.20322622e-01j
  3.41852322e-01-4.20322622e-01j  3.11647256e-01+0.00000000e+00j
  9.42698277e-02+6.34745355e-01j  9.42698277e-02-6.34745355e-01j
  7.99416256e-02+0.00000000e+00j  5.27374757e-02-7.32437041e-03j
  5.27374757e-02+7.32437041e-03j  2.34227771e-02+0.00000000e+00j
  1.60886674e-02+0.00000000e+00j  1.14665173e-02+0.00000000e+00j
  5.48931167e-03+0.00000000e+00j  1.89828846e-03+2.87560025e-03j
  1.89828846e-03-2.87560025e-03j  9.51177675e-04+0.00000000e+00j
  2.79494911e-04+9.11518753e-05j  2.79494911e-04-9.11518753e-05j
  2.60675127e-04+0.000000

In [12]:
from koopmanlib.solver_1 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 29s 5s/step - loss: 0.9189 - val_loss: 0.9094
Epoch 2/2
2/2 [==============================] - 0s 283ms/step - loss: 0.9119 - val_loss: 0.9170
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 1s 300ms/step - loss: 0.9172 - val_loss: 0.9243
Epoch 2/2
2/2 [==============================] - 0s 277ms/step - loss: 0.9108 - val_loss: 0.9196
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 308ms/step - loss: 0.9173 - val_loss: 0.9070
Epoch 2/2
2/2 [==============================] - 0s 287ms/step - loss: 0.9162 - val_loss: 0.9115
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 296ms/step - loss: 0.9189 - val_loss: 0.9179
Epoch 2/2
2/2 [==============================] - 0s 275ms/step - loss: 0.9101 - val_loss: 0.9102
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 1s 311ms/step - loss: 0.9098 - val_loss: 0.9102
Epoch 2/2
2/2 [==

In [13]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs1 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs1['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs1['resDMD_DL_outputs']['efuns'].shape)

[ 1.00654430e+00+0.00000000e+00j  9.99945847e-01+0.00000000e+00j
  8.42447616e-01+6.38838064e-03j  8.42447616e-01-6.38838064e-03j
  8.12492000e-01-2.16954345e-01j  8.12492000e-01+2.16954345e-01j
  7.80877161e-01+3.95361865e-01j  7.80877161e-01-3.95361865e-01j
  6.43019109e-01-4.97296435e-01j  6.43019109e-01+4.97296435e-01j
  5.05590367e-01+0.00000000e+00j  5.04682776e-01+1.48117767e-01j
  5.04682776e-01-1.48117767e-01j  3.45120915e-01-4.33516486e-01j
  3.45120915e-01+4.33516486e-01j  2.07514178e-01+5.16819474e-02j
  2.07514178e-01-5.16819474e-02j  1.28092242e-01+3.03181672e-01j
  1.28092242e-01-3.03181672e-01j  1.70198927e-02+1.72888969e-03j
  1.70198927e-02-1.72888969e-03j  1.19871459e-02+0.00000000e+00j
  1.08145534e-02-1.46810474e-02j  1.08145534e-02+1.46810474e-02j
  1.57908919e-03+0.00000000e+00j  1.14434970e-03+1.98952735e-03j
  1.14434970e-03-1.98952735e-03j  7.63728037e-04+2.65975489e-04j
  7.63728037e-04-2.65975489e-04j  1.95766044e-04+0.00000000e+00j
  3.08920704e-05+0.000000

In [10]:
from koopmanlib.solver_2 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 248ms/step - loss: 175698.2031 - val_loss: 138815.8438
Epoch 2/2
2/2 [==============================] - 0s 94ms/step - loss: 160264.8929 - val_loss: 132769.2031
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 119ms/step - loss: 154535.5312 - val_loss: 128537.4844
Epoch 2/2
2/2 [==============================] - 0s 93ms/step - loss: 151040.9754 - val_loss: 125582.9922
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 111ms/step - loss: 144064.6205 - val_loss: 122888.4844
Epoch 2/2
2/2 [==============================] - 0s 91ms/step - loss: 143580.1897 - val_loss: 120373.7578
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 112ms/step - loss: 142899.1652 - val_loss: 118060.5391
Epoch 2/2
2/2 [==============================] - 0s 91ms/step - loss: 139898.2589 - val_loss: 115985.0703
number of the outer loop: 3
Epoch 1/2
2/2 [=====================

In [11]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs2 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs2['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs2['resDMD_DL_outputs']['efuns'].shape)

[ 1.00009814e+00+0.00000000e+00j  9.23230504e-01+0.00000000e+00j
  8.49931379e-01+0.00000000e+00j  8.15968192e-01+0.00000000e+00j
  7.50240519e-01+1.96689347e-01j  7.50240519e-01-1.96689347e-01j
  7.14012424e-01+3.76691953e-01j  7.14012424e-01-3.76691953e-01j
  5.44271147e-01+5.33440648e-01j  5.44271147e-01-5.33440648e-01j
  2.17373699e-01+1.10572223e-01j  2.17373699e-01-1.10572223e-01j
  7.97144644e-02+9.24875524e-02j  7.97144644e-02-9.24875524e-02j
  6.02304742e-02+1.62717759e-02j  6.02304742e-02-1.62717759e-02j
  5.17125988e-02+2.57411630e-01j  5.17125988e-02-2.57411630e-01j
  3.08942306e-02+0.00000000e+00j  6.85356377e-03+0.00000000e+00j
  4.14991555e-03+0.00000000e+00j  5.62444867e-04+0.00000000e+00j
  3.20907673e-04+6.14236226e-04j  3.20907673e-04-6.14236226e-04j
  1.57362134e-04+0.00000000e+00j  1.07278147e-04+0.00000000e+00j
  7.95632342e-05+0.00000000e+00j  3.26646842e-05+0.00000000e+00j
  3.11175320e-05-1.01300774e-04j  3.11175320e-05+1.01300774e-04j
  1.81251623e-05+0.000000

In [8]:
from koopmanlib.solver_3 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 257ms/step - loss: 0.0632 - val_loss: 0.0626
Epoch 2/2
2/2 [==============================] - 0s 97ms/step - loss: 0.0640 - val_loss: 0.0609
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 120ms/step - loss: 0.0630 - val_loss: 0.0608
Epoch 2/2
2/2 [==============================] - 0s 91ms/step - loss: 0.0629 - val_loss: 0.0600
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 114ms/step - loss: 0.0625 - val_loss: 0.0603
Epoch 2/2
2/2 [==============================] - 0s 92ms/step - loss: 0.0626 - val_loss: 0.0594
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 116ms/step - loss: 0.0621 - val_loss: 0.0598
Epoch 2/2
2/2 [==============================] - 0s 98ms/step - loss: 0.0621 - val_loss: 0.0593
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 111ms/step - loss: 0.0618 - val_loss: 0.0595
Epoch 2/2
2/2 [====

In [9]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs3 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs3['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs3['resDMD_DL_outputs']['efuns'].shape)

[ 1.00002718e+00+0.00000000e+00j  9.56089623e-01+0.00000000e+00j
  8.13690285e-01+0.00000000e+00j  7.84476296e-01-1.58947626e-01j
  7.84476296e-01+1.58947626e-01j  7.07538308e-01-3.49715399e-01j
  7.07538308e-01+3.49715399e-01j  6.09396340e-01-4.73432819e-01j
  6.09396340e-01+4.73432819e-01j  5.81265573e-01-2.97293606e-02j
  5.81265573e-01+2.97293606e-02j  3.05806995e-01+4.77298243e-01j
  3.05806995e-01-4.77298243e-01j  2.48236611e-01+0.00000000e+00j
  7.71992856e-02-3.69864411e-01j  7.71992856e-02+3.69864411e-01j
  5.97934189e-02+0.00000000e+00j  1.48508155e-02+2.64026950e-02j
  1.48508155e-02-2.64026950e-02j  1.19782696e-02+0.00000000e+00j
  8.60010482e-03+0.00000000e+00j  5.78851949e-03+0.00000000e+00j
  1.06344945e-03+4.76597366e-03j  1.06344945e-03-4.76597366e-03j
  6.45385304e-04-7.26147043e-04j  6.45385304e-04+7.26147043e-04j
  5.29906094e-04+0.00000000e+00j  7.99680180e-05+0.00000000e+00j
  2.63641837e-05+1.67314624e-04j  2.63641837e-05-1.67314624e-04j
  1.75773173e-05+5.525044

In [6]:
from koopmanlib.solver_4 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 292ms/step - loss: 0.8457 - val_loss: 0.1185
Epoch 2/2
2/2 [==============================] - 0s 95ms/step - loss: 0.0988 - val_loss: 6.0117e-04
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 112ms/step - loss: 0.5756 - val_loss: 0.2213
Epoch 2/2
2/2 [==============================] - 0s 97ms/step - loss: 0.4154 - val_loss: 0.3390
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 114ms/step - loss: 0.6160 - val_loss: 0.1162
Epoch 2/2
2/2 [==============================] - 0s 97ms/step - loss: 1.8418 - val_loss: 0.2435
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 125ms/step - loss: 1.0422 - val_loss: 0.0228
Epoch 2/2
2/2 [==============================] - 0s 101ms/step - loss: 0.8035 - val_loss: 0.3174
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 116ms/step - loss: 0.4993 - val_loss: 0.0767
Epoch 2/2
2/2 

In [7]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs4 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs4['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs4['resDMD_DL_outputs']['efuns'].shape)

[ 1.02604228e+00+0.00000000e+00j  9.99998575e-01+0.00000000e+00j
  8.52681838e-01-1.53050877e-01j  8.52681838e-01+1.53050877e-01j
  7.47948473e-01+4.64294975e-01j  7.47948473e-01-4.64294975e-01j
  7.00210276e-01-2.58646967e-01j  7.00210276e-01+2.58646967e-01j
  5.78783659e-01+0.00000000e+00j  3.76999386e-01+5.39944605e-01j
  3.76999386e-01-5.39944605e-01j  9.15988535e-02+0.00000000e+00j
  4.09666129e-02+4.65380017e-02j  4.09666129e-02-4.65380017e-02j
  1.37836541e-02+0.00000000e+00j  1.21044224e-02+6.42996196e-01j
  1.21044224e-02-6.42996196e-01j  3.20955606e-03+0.00000000e+00j
  7.56921525e-04-3.86733955e-04j  7.56921525e-04+3.86733955e-04j
  1.37422082e-04+0.00000000e+00j  1.11408236e-04+1.62545280e-05j
  1.11408236e-04-1.62545280e-05j  1.03639548e-04+4.26908050e-04j
  1.03639548e-04-4.26908050e-04j  1.79213432e-05+0.00000000e+00j
  2.94790521e-06+0.00000000e+00j  1.69377085e-06+2.52996392e-06j
  1.69377085e-06-2.52996392e-06j  1.51754942e-06+3.57410785e-07j
  1.51754942e-06-3.574107